In [1]:
from datasets import load_dataset

dataset = load_dataset('taln-ls2n/semeval-2010-pre')

No config specified, defaulting to: sem_eval/raw
Reusing dataset sem_eval (/Users/boudin-f/.cache/huggingface/datasets/taln-ls2n___sem_eval/raw/1.0.0/b40e008b5c96137733e24d9d244d70aa1fe6353ee65e180d8f6948af4027fbe4)


  0%|          | 0/2 [00:00<?, ?it/s]

In [2]:
from tqdm.notebook import tqdm

P, R, M, U, nb_kps = [], [], [], [], []
    
for sample in tqdm(dataset['test']):
    nb_kps.append(len(sample["keyphrases"]))
    P.append(sample["prmu"].count("P") / nb_kps[-1])
    R.append(sample["prmu"].count("R") / nb_kps[-1])
    M.append(sample["prmu"].count("M") / nb_kps[-1])
    U.append(sample["prmu"].count("U") / nb_kps[-1])
        
print("# keyphrases: {:.2f}".format(sum(nb_kps)/len(nb_kps)))
print("% P: {:.2f}".format(sum(P)/len(P)*100))
print("% R: {:.2f}".format(sum(R)/len(R)*100))
print("% M: {:.2f}".format(sum(M)/len(M)*100))
print("% U: {:.2f}".format(sum(U)/len(U)*100))

  0%|          | 0/100 [00:00<?, ?it/s]

# keyphrases: 14.66
% P: 40.11
% R: 8.34
% M: 27.12
% U: 24.43


In [3]:
import spacy

nlp = spacy.load("en_core_web_sm")

# https://spacy.io/usage/linguistic-features#native-tokenizer-additions

from spacy.lang.char_classes import ALPHA, ALPHA_LOWER, ALPHA_UPPER
from spacy.lang.char_classes import CONCAT_QUOTES, LIST_ELLIPSES, LIST_ICONS
from spacy.util import compile_infix_regex

# Modify tokenizer infix patterns
infixes = (
    LIST_ELLIPSES
    + LIST_ICONS
    + [
        r"(?<=[0-9])[+\-\*^](?=[0-9-])",
        r"(?<=[{al}{q}])\.(?=[{au}{q}])".format(
            al=ALPHA_LOWER, au=ALPHA_UPPER, q=CONCAT_QUOTES
        ),
        r"(?<=[{a}]),(?=[{a}])".format(a=ALPHA),
        # ✅ Commented out regex that splits on hyphens between letters:
        # r"(?<=[{a}])(?:{h})(?=[{a}])".format(a=ALPHA, h=HYPHENS),
        r"(?<=[{a}0-9])[:<>=/](?=[{a}])".format(a=ALPHA),
    ]
)

infix_re = compile_infix_regex(infixes)
nlp.tokenizer.infix_finditer = infix_re.finditer

In [4]:
doc_len = []
for sample in tqdm(dataset['test']):
    doc_len.append(len(nlp(sample["title"])) + len(nlp(sample["abstract"])))
        
print("avg doc len: {:.1f}".format(sum(doc_len)/len(doc_len)))        

  0%|          | 0/100 [00:00<?, ?it/s]

avg doc len: 203.1
